# **FALL 2023 EPS 109 Final Project - NbCS Synthetic Control Basline Simulation**

### LIBRARY IMPORTS AND EARTH ENGINE INITIALIZATION
***

In [ ]:
# import general libraries
import numpy as np
import pandas as pd
import os
import random
import geopy.distance
import SparseSC

# import google libraries
from google.colab import drive
drive.mount('/content/drive')

# import visualization libraries
import matplotlib.pyplot as plt
import seaborn as sns
import geemap
#!pip install scikit-learn==1.1

In [ ]:
# import authorize and initialize google earth engine
import ee
!earthengine authenticate
ee.Initialize()

In [ ]:
# set constants
KML_FOLDER_PATH = '/content/drive/MyDrive/your_data_path_here'

### KML TO EE.FEATURE_COLLECTION CONVERSION
***

In [ ]:
# get list of KML files
kml_files = [file for file in os.listdir(KML_FOLDER_PATH) if file.endswith('.kml')]

# create dictionary of ee.FeatureCollections and list of unsuccessful KML conversions
feature_collections = {}

#for i in range(len(kml_files))
#    file_path = os.path.join(KML_FOLDER_PATH, kml_files[i])
#    proj_id = kml_files[i][:-4]
#    ee_fs = geemap.kml_to_ee(file_path)
#    feature_collections[proj_id] = ee_fs

file_path = os.path.join(KML_FOLDER_PATH, kml_files[2])
proj_id = kml_files[2][:-4]
ee_fs = geemap.kml_to_ee(file_path)
feature_collections[proj_id] = ee_fs

### PROJECT DONOR CREATION
***

In [ ]:
def create_donors(fc, num_donors=1000, buffer_radius=5000):
    """
    Creates 1000 "donor" sites around the project area for a synthetic baseline.

    Args:
        fc (ee.FeatureCollection) -> An Earth Engine Feature Collection of the project area.
        num_donors (int) -> The number of donor sites to create.
        buffer_radius (int) -> The radius of the surrounding area to create donor sites in (meters).
    Returns:
        donors (list of ee.FeatureCollections) -> A length 1000 list containing the donor sites.
    """
    try:
        proj_area = fc.geometry().area(maxError=1).getInfo()
        proj_center_coords = fc.geometry().centroid(maxError=1).getInfo()['coordinates'] # [lon, lat]
    except ee.EEException as e:
        if "Request payload size exceeds the limit" in str(e):
            print("Skipping project: Request payload size exceeds the limit")
        return

    proj_center = geopy.Point(proj_center_coords[1], proj_center_coords[0])
    donor_radius = np.sqrt(proj_area / np.pi)
    donors = {}

    for i in range(1, num_donors + 1):
        rand_angle = random.uniform(0, 365)
        rand_dist = random.uniform(donor_radius, buffer_radius)

        dist = geopy.distance.distance(meters=rand_dist)
        new_point = dist.destination(point=proj_center, bearing=rand_angle)

        new_lon = new_point.longitude
        new_lat = new_point.latitude

        new_point = ee.Geometry.Point([new_lon, new_lat]) # [lon, lat]
        new_donor = new_point.buffer(donor_radius)

        donors[str(i)] = new_donor

    return donors

In [ ]:
areas = {'0': feature_collections['VCS1115']}

for proj_id, proj_ee in feature_collections.items():
    areas.update(create_donors(proj_ee, num_donors=100))

In [ ]:
# create output df
sc_data = {
    "area id": [],
    "year": [],
    "annual deforestation": [],
}

sc_data = pd.DataFrame(sc_data)

### PROJECT DEFORESATION ESTIMATION WITH GOOGLE EARTH ENGINE
***

In [ ]:
def estimate_aad(fc, start_year=0, end_year='2022'):
    """
    Estimates the average annual deforestation (AAD) within the boundaries of an
    ee.FeatureCollection over a specified period of time by accessing the Hansen et al.
    Global Forest Change dataset.

    Args:
        fc (ee.FeatureCollection) -> An ee.FeatureCollection of the project area.
        start_year (string) -> A string representing the start year in the format "YYYY".
        end_year (string) -> A string representing the end year in the format "YYYY".
    Returns:
        mean_annual_loss (float) -> The average annual deforestation in square meters of fc.
    """

    # load the Global Forest Change dataset, including loss and lossyear
    gfc_image = ee.Image("UMD/hansen/global_forest_change_2022_v1_10")
    loss_image = gfc_image.select('loss').clip(fc) # loss per pixel
    loss_area = loss_image.multiply(ee.Image.pixelArea()) # loss per square meter
    loss_year = gfc_image.select('lossyear')

    # calculate total deforestation within the project area
    try:
        loss_by_year = ee.List(loss_area.addBands(loss_year).reduceRegion(
            reducer=ee.Reducer.sum().group(groupField=1),
            geometry=fc,
            scale=30,
            maxPixels=1e10
        ).get('groups')).getInfo()

        return loss_by_year[start_year]['sum']
    except ee.EEException as e:
        if "Request payload size exceeds the limit" in str(e):
            print("Skipping project: Request payload size exceeds the limit")
        return

    start_since_2000 = int(start_year) % 2000
    end_since_2000 = int(end_year) % 2000

    # calculate the total and mean forest loss
    total_loss = 0
    for i in range(min(end_since_2000 - start_since_2000, len(loss_by_year))):
        total_loss += loss_by_year[start_since_2000 + i]['sum']
    mean_annual_loss = total_loss / (end_since_2000 - start_since_2000)
    return mean_annual_loss

In [ ]:
for area_id in areas:
    for year in range(1, 22):
        cur_defo = estimate_aad(areas[area_id], start_year=year)
        sc_data = sc_data.append({"area id": area_id, "year": year, "annual deforestation": cur_defo}, ignore_index=True)

### SYNTHETIC CONTROL - DEFORESTATION SIMULATION
***

In [ ]:
sc_data_pivot = sc_data.pivot(index='area id', columns='year', values='annual deforestation')
sc_data_pivot.head()

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

In [ ]:
with writer.saving(fig, "nbcs_test1.mp4", dpi=200):
    for i in range(10, 100):
        sc_data_pivot = sc_data.pivot(index='area id', columns='year', values='annual deforestation')
        sc_data_pivot = sc_data_pivot.head(i)

        features = sc_data_pivot.iloc[:, sc_data_pivot.columns <= 10].values
        targets = sc_data_pivot.iloc[:, sc_data_pivot.columns > 10].values
        treated_units = [idx for idx, val in enumerate(sc_data_pivot.index.values) if val == '0']

        sc_model = SparseSC.fit_fast(features=features, targets=targets, treated_units=treated_units, gradient_folds=2)

        result = sc_data_pivot.loc[sc_data_pivot.index == '0'].T.reset_index(drop=False)
        result.columns = ['year', 'observed']
        result['synthetic'] = sc_model.predict(sc_data_pivot.values)[treated_units, :][0]


        fig.clear()
        x = np.arange(1, 22)
        ax = fig.add_subplot()
        ax.plot(x, result['observed'], label='observed')
        ax.plot(x, result['synthetic'], label='synthetic')
        ax.axvline(x=10, color='black', linestyle='--', label='Project Start')

        ax.set_title("Average Annual Deforestation - Observed vs. Synthetic Control Project Area")
        ax.set_xlabel("Years (since 2000)")
        ax.set_ylabel("Average Annual Deforestation (m^2)")
        ax.legend()

        plt.draw()
        writer.grab_frame()

### SYNTHETIC CONTROL DONOR SITE VISUALIZATION
***

In [ ]:
Map = geemap.Map()
Map.add_layer(feature_collections['VCS1115'])

vcs1115_donors = create_donors(feature_collections['VCS1115'], num_donors=10, buffer_radius=400000)

for donor_id, donor_ee in vcs1115_donors.items():
    Map.add_layer(donor_ee, opacity=0.8)

Map.centerObject(feature_collections['VCS1115'], zoom=10)
Map